In [151]:
import pandas as pd
import numpy as np

from dynamic_prediction import features

df = pd.read_csv(r"C:\Users\Arun\Downloads\data.csv")
df.head()

date      price  bedrooms  bathrooms  sqft_living  sqft_lot  \
0  2014-05-02 00:00:00   313000.0       3.0       1.50         1340      7912   
1  2014-05-02 00:00:00  2384000.0       5.0       2.50         3650      9050   
2  2014-05-02 00:00:00   342000.0       3.0       2.00         1930     11947   
3  2014-05-02 00:00:00   420000.0       3.0       2.25         2000      8030   
4  2014-05-02 00:00:00   550000.0       4.0       2.50         1940     10500   

   floors  waterfront  view  condition  sqft_above  sqft_basement  yr_built  \
0     1.5           0     0          3        1340              0      1955   
1     2.0           0     4          5        3370            280      1921   
2     1.0           0     0          4        1930              0      1966   
3     1.0           0     0          4        1000           1000      1963   
4     1.0           0     0          4        1140            800      1976   

   yr_renovated                    street       city  statezip country  
0          2005      18810 Densmore Ave N  Shoreline  WA 98133     USA  
1             0           709 W Blaine St    Seattle  WA 98119     USA  
2             0  26206-26214 143rd Ave SE       Kent  WA 98042     USA  
3             0           857 170th Pl NE   Bellevue  WA 98008     USA  
4          1992         9105 170th Ave NE    Redmond  WA 98052     USA

In [152]:
df["house_age"] = 2025 - df["yr_built"]
df["renovated_flag"] = (df["yr_renovated"] > 0).astype(int)

In [153]:
df.drop(columns=["date","country","sqft_above","yr_built","yr_renovated","statezip"],axis = 1,inplace=True)
df["sqft_basement"]=np.where(df["sqft_basement"]>0,1,0)

In [154]:
# from ydata_profiling import ProfileReport
#
# report = ProfileReport(df,explorative=True)
# report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 14/14 [00:00<00:00, 184.06it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [155]:
df.head()

price  bedrooms  bathrooms  sqft_living  sqft_lot  floors  waterfront  \
0   313000.0       3.0       1.50         1340      7912     1.5           0   
1  2384000.0       5.0       2.50         3650      9050     2.0           0   
2   342000.0       3.0       2.00         1930     11947     1.0           0   
3   420000.0       3.0       2.25         2000      8030     1.0           0   
4   550000.0       4.0       2.50         1940     10500     1.0           0   

   view  condition  sqft_basement                    street       city  \
0     0          3              0      18810 Densmore Ave N  Shoreline   
1     4          5              1           709 W Blaine St    Seattle   
2     0          4              0  26206-26214 143rd Ave SE       Kent   
3     0          4              1           857 170th Pl NE   Bellevue   
4     0          4              1         9105 170th Ave NE    Redmond   

   house_age  renovated_flag  
0         70               1  
1        104               0  
2         59               0  
3         62               0  
4         49               1

In [156]:
def outlier(df):
    for col in df.select_dtypes(include=["float64","int64","int32"]).columns:
        q1 = df[col].quantile(0.25)
        q3 = df[col].quantile(0.75)
        iqr = q3-q1
        lower = q1 - 1.5* iqr
        upper = q3 + 1.5* iqr
        df[col]=np.where(df[col]<lower,lower,np.where(df[col]>upper,upper,df[col]))
    return df

In [157]:
df=outlier(df)

In [158]:
from sklearn.compose import make_column_transformer
from sklearn.preprocessing import OneHotEncoder, StandardScaler, PolynomialFeatures
from imblearn.pipeline import make_pipeline
from imblearn.over_sampling import SMOTE

In [159]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4600 entries, 0 to 4599
Data columns (total 14 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   price           4600 non-null   float64
 1   bedrooms        4600 non-null   float64
 2   bathrooms       4600 non-null   float64
 3   sqft_living     4600 non-null   float64
 4   sqft_lot        4600 non-null   float64
 5   floors          4600 non-null   float64
 6   waterfront      4600 non-null   float64
 7   view            4600 non-null   float64
 8   condition       4600 non-null   float64
 9   sqft_basement   4600 non-null   float64
 10  street          4600 non-null   object 
 11  city            4600 non-null   object 
 12  house_age       4600 non-null   float64
 13  renovated_flag  4600 non-null   float64
dtypes: float64(12), object(2)
memory usage: 503.2+ KB


In [160]:
class linearregression:
    def __init__(self,epochs=500,lr=0.09):
        self.intercept=None
        self.coef=None
        self.epochs=epochs
        self.lr=lr
    def fit(self,x_train,y_train):
        self.coef=np.ones(x_train.shape[1])
        self.intercept=0
        for i in range(self.epochs):
            y_hat = np.dot(x_train,self.coef)+self.intercept
            slope_der = -2 * np.mean(y_train - y_hat)
            self.intercept-= self.lr*slope_der
            slope_coef = -2 * np.dot((y_train-y_hat),x_train)/x_train.shape[0]
            self.coef-= self.lr*slope_coef
    def predict(self,x_test):
        return np.dot(x_test,self.coef) + self.intercept


In [161]:
def split(df):
    y = df["price"]
    x = df.drop("price", axis=1)
    size = len(df)
    training_size = int(size * 0.8)

    x_train = x.iloc[:training_size, :]
    x_test = x.iloc[training_size:, :]
    y_train = y.iloc[:training_size]
    y_test = y.iloc[training_size:]

    return x_train, x_test, y_train, y_test
x_train,x_test,y_train,y_test=split(df)

In [162]:
df.columns

Index(['price', 'bedrooms', 'bathrooms', 'sqft_living', 'sqft_lot', 'floors',
       'waterfront', 'view', 'condition', 'sqft_basement', 'street', 'city',
       'house_age', 'renovated_flag'],
      dtype='object')

In [163]:
poly_pipe = make_pipeline(
    StandardScaler(),
    PolynomialFeatures(degree=2, include_bias=False)
)

In [164]:
transform= make_column_transformer(
    (OneHotEncoder(sparse_output=False,handle_unknown="ignore"),['street', 'city']),
    (StandardScaler(),[ 'bedrooms', 'bathrooms', 'sqft_living', 'sqft_lot', 'floors',
       'waterfront', 'view', 'condition',  'sqft_basement',"house_age","renovated_flag"
       ]),
    (poly_pipe, ['bathrooms', 'sqft_living']),
    remainder="passthrough"
)

In [165]:
from sklearn.preprocessing import PolynomialFeatures

In [166]:
pipeline=make_pipeline(
    transform,
    linearregression()
)

In [167]:
y_train=np.array(y_train)
y_train.shape

(3680,)

In [168]:
pipeline.fit(x_train,y_train)

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('onehotencoder',
                                                  OneHotEncoder(handle_unknown='ignore',
                                                                sparse_output=False),
                                                  ['street', 'city']),
                                                 ('standardscaler',
                                                  StandardScaler(),
                                                  ['bedrooms', 'bathrooms',
                                                   'sqft_living', 'sqft_lot',
                                                   'floors', 'waterfront',
                                                   'view', 'condition',
                                                   'sqft_basement', 'house_age',
                                                   'renovated_flag']),
                                                 ('pipeline',
                                                  Pipeline(steps=[('standardscaler',
                                                                   StandardScaler()),
                                                                  ('polynomialfeatures',
                                                                   PolynomialFeatures(include_bias=False))]),
                                                  ['bathrooms',
                                                   'sqft_living'])])),
                ('linearregression',
                 <__main__.linearregression object at 0x000001AE53660FA0>)])

In [169]:
y_pred=pipeline.predict(x_test)

C:\Users\Arun\AppData\Roaming\Python\Python310\site-packages\imblearn\pipeline.py:65: FutureWarning: This Pipeline instance is not fitted yet. Call 'fit' with appropriate arguments before using other methods such as transform, predict, etc. This will raise an error in 0.15 instead of the current warning.
  warnings.warn(


In [170]:
from sklearn.metrics import r2_score,mean_squared_error
print(r2_score(y_test,y_pred))
print(mean_squared_error(y_test,y_pred))

0.3423063565428487
54167929117.94031


In [178]:
from catboost import CatBoostRegressor

new_pipeline = make_pipeline(
    transform,
    CatBoostRegressor(task_type="GPU")
)

In [179]:
new_pipeline.fit(x_train,y_train)

Learning rate set to 0.047911
0:	learn: 247789.9238826	total: 16ms	remaining: 16s
1:	learn: 241073.0153305	total: 31.2ms	remaining: 15.6s
2:	learn: 235192.9640213	total: 46.7ms	remaining: 15.5s
3:	learn: 229670.9060735	total: 61.4ms	remaining: 15.3s
4:	learn: 224556.2394369	total: 76ms	remaining: 15.1s
5:	learn: 219905.5509992	total: 90.2ms	remaining: 14.9s
6:	learn: 215327.0584225	total: 106ms	remaining: 15.1s
7:	learn: 210853.1539288	total: 123ms	remaining: 15.2s
8:	learn: 206742.8843545	total: 137ms	remaining: 15s
9:	learn: 202459.4182314	total: 167ms	remaining: 16.5s
10:	learn: 198356.9514251	total: 182ms	remaining: 16.4s
11:	learn: 194982.3925653	total: 200ms	remaining: 16.4s
12:	learn: 191738.1226243	total: 214ms	remaining: 16.3s
13:	learn: 188751.7190559	total: 231ms	remaining: 16.3s
14:	learn: 185727.3391532	total: 248ms	remaining: 16.3s
15:	learn: 182939.7410308	total: 263ms	remaining: 16.2s
16:	learn: 180268.7185627	total: 278ms	remaining: 16.1s
17:	learn: 177938.2513754	tota

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('onehotencoder',
                                                  OneHotEncoder(handle_unknown='ignore',
                                                                sparse_output=False),
                                                  ['street', 'city']),
                                                 ('standardscaler',
                                                  StandardScaler(),
                                                  ['bedrooms', 'bathrooms',
                                                   'sqft_living', 'sqft_lot',
                                                   'floors', 'waterfront',
                                                   'view', 'condition',
                                                   'sqft_basement', 'house_age',
                                                   'renovated_flag']),
                                                 ('pipeline',
                                                  Pipeline(steps=[('standardscaler',
                                                                   StandardScaler()),
                                                                  ('polynomialfeatures',
                                                                   PolynomialFeatures(include_bias=False))]),
                                                  ['bathrooms',
                                                   'sqft_living'])])),
                ('catboostregressor',
                 <catboost.core.CatBoostRegressor object at 0x000001AE536BE980>)])

In [180]:
pred=new_pipeline.predict(x_test)

In [181]:
print(r2_score(y_test,pred))
print(mean_squared_error(y_test,pred))

0.3359057058436479
54695089440.73213


In [186]:
import pickle
pickle.dump(pipeline,open("model.pickle","wb"))